This is the initial notebook to explore the data and run the first models. 

In [1]:
import pandas as pd
import numpy as np

from sklearn.impute import SimpleImputer
from sklearn.ensemble import RandomForestRegressor
import xgboost as xgb
from sklearn.preprocessing import OneHotEncoder

from fastai.imports import *
from fastai.tabular.all import *

from numpy import random
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_squared_log_error
from sklearn import metrics
from sklearn.model_selection import KFold, cross_val_score
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler

import eli5
from eli5.sklearn import PermutationImportance


from scipy.stats import skew, norm
from catboost import CatBoostRegressor
from feature_engine.transformation import YeoJohnsonTransformer
from category_encoders.binary import BinaryEncoder

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

In [2]:
import shap
import xgboost
from sklearn.svm import SVR
from lightgbm import LGBMRegressor
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeRegressor
from mlxtend.regressor import StackingRegressor
from sklearn.linear_model import LinearRegression, BayesianRidge
from sklearn.model_selection import RepeatedKFold
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.ensemble import VotingRegressor
from sklearn.kernel_ridge import KernelRidge
from sklearn.linear_model import Ridge, RidgeCV
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import scale
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.decomposition import PCA
from mlxtend.regressor import StackingCVRegressor

In [3]:
test = pd.read_csv('test.csv')
sample = pd.read_csv('sample_submission.csv')
train = pd.read_csv('train.csv')

In [4]:
train.shape, test.shape

((1460, 81), (1459, 80))

Based on initial analysis the train and test datasets have similar characteristics, so it will be easier to combine them for imputation and data analysis work. 

In [5]:
train_test = pd.concat([train, test], ignore_index=True)

In [6]:
train_test.shape

(2919, 81)

In [7]:
pd.isnull(train_test).sum()[pd.isnull(train_test).sum() > 0]

MSZoning           4
LotFrontage      486
Alley           2721
Utilities          2
Exterior1st        1
Exterior2nd        1
MasVnrType        24
MasVnrArea        23
BsmtQual          81
BsmtCond          82
BsmtExposure      82
BsmtFinType1      79
BsmtFinSF1         1
BsmtFinType2      80
BsmtFinSF2         1
BsmtUnfSF          1
TotalBsmtSF        1
Electrical         1
BsmtFullBath       2
BsmtHalfBath       2
KitchenQual        1
Functional         2
FireplaceQu     1420
GarageType       157
GarageYrBlt      159
GarageFinish     159
GarageCars         1
GarageArea         1
GarageQual       159
GarageCond       159
PoolQC          2909
Fence           2348
MiscFeature     2814
SaleType           1
SalePrice       1459
dtype: int64

It looks like Alley, FireplaceQu, PoolQC, Fence and MiscFeature have significant numbers of missing data. So it will be best to eliminate those rows. There are a number of rows that have less than 5 rows with missing data. Since some of these are categorical and some are continuous data, their missing data will be replaced with the most frequent value. 

Instead, for high_nan, replace the NaN with None; since they don't have that feature. 

In [8]:
drop_high_nan=['Alley','FireplaceQu','PoolQC','Fence','MiscFeature']
#train_test=train_test.drop(drop_high_nan,axis=1)
train_test[drop_high_nan] = train_test[drop_high_nan].fillna('None')


small_nan_cols = ['MSZoning', 'Utilities', 'Exterior1st', 'Exterior2nd', 'BsmtFinSF1', 'BsmtFinSF2', 'BsmtUnfSF', 
                  'TotalBsmtSF', 'Electrical', 'BsmtFullBath', 'BsmtHalfBath', 'KitchenQual', 'Functional', 'GarageCars', 
                  'GarageArea','SaleType', 'SaleCondition']
small_impute = SimpleImputer(strategy='most_frequent')
train_test[small_nan_cols] = pd.DataFrame(small_impute.fit_transform(train_test[small_nan_cols]),columns=small_nan_cols)

The following columns seem to have one value significantly larger than the rest, and it would probably be best to use the mode, or most common, value to feel each NaN value: MasVnrType, MasVnrArea, BsmtCond, BsmtExposure, BsmtFinType2, GarageType, GarageFinish, GarageQual, and GarageCond. That is represents 9 out of the 13 columns. 

BsmtQual has two values larger than the rest: Gd and TA. But it only has 2.8% NaNs, so simply using the mode might be good enough.  

GarageYrBlt has 59 NaNs out 2919 rows which is only 2%. It has a dispersed set of values, so it might be easiest just to have any NaNs have the same value as YearBuilt. 

BsmtFinType1 has only 2.7% value of NaNs, and most two of its largest values are GLQ and Unf. It might be easiest to use the mode here. 

LotFrontage has 486 NaNs out of 2919 rows which is a pretty high 16.7%. It has a dispersed range of values, but looking at its characteristics from the describe function above, it seems to have a pretty even distribution with a mean of 10,168 and a median of 9,453. So using the mean to fill in the NaNs seems reasonable. If it turns out this value has a high impact on the predictability of the SalePrice, then it might be good to revisit this assumption. 

In [9]:
#mode_cols = ['MasVnrType', 'MasVnrArea', 'BsmtCond', 'BsmtExposure', 'BsmtFinType2', 'GarageType', 'GarageFinish', 
#             'GarageQual','GarageCond', 'BsmtQual', 'BsmtFinType1']
mode_cols = ['MasVnrType', 'MasVnrArea', 'BsmtCond', 'BsmtExposure', 'BsmtFinType2', 'BsmtQual', 'BsmtFinType1']
mode_impute = SimpleImputer(strategy='most_frequent')
train_test[mode_cols] = pd.DataFrame(mode_impute.fit_transform(train_test[mode_cols]),columns=mode_cols)

garage_cols = ['GarageType', 'GarageFinish', 'GarageQual','GarageCond', 'GarageYrBlt']
train_test[garage_cols] = train_test[garage_cols].fillna('None')

train_test['LotFrontage'].fillna((train_test['LotFrontage'].mean()), inplace=True)
#train_test['GarageYrBlt'] = train_test['GarageYrBlt'].fillna(train_test['YearBuilt'])

In [10]:
pd.isnull(train_test).sum()[pd.isnull(train_test).sum() > 0]

SalePrice    1459
dtype: int64

In [11]:
train_test['BsmtQual'].unique()

array(['Gd', 'TA', 'Ex', 'Fa'], dtype=object)

In [12]:
train_test['BsmtFinType1'].unique()

array(['GLQ', 'ALQ', 'Unf', 'Rec', 'BLQ', 'LwQ'], dtype=object)

In [13]:
train_test.BsmtQual = train_test.BsmtQual.replace({"Ex": 110, "Gd": 95, "TA": 85, "Fa": 75, "Po": 60, "NA": 0})
train_test.BsmtFinType1 = train_test.BsmtFinType1.replace({"GLQ": 6, "ALQ": 5, "BLQ": 4, "Rec": 3, "LwQ": 2, "Unf": 1,
                                                         "NA": 0})

To look at how many features have a skew above 0.6, since high skew can be an issue in regression analysis. 

In [14]:
number_cols = train_test.select_dtypes(include=np.number).columns.tolist()

In [15]:
skew_features = train_test[number_cols].apply(lambda x: skew(x)).sort_values(ascending=False)
high_skew = skew_features[skew_features > 0.6]
skew_index = high_skew.index
skew_index

Index(['MiscVal', 'PoolArea', 'LotArea', 'LowQualFinSF', '3SsnPorch',
       'KitchenAbvGr', 'EnclosedPorch', 'ScreenPorch', 'OpenPorchSF',
       'WoodDeckSF', 'LotFrontage', '1stFlrSF', 'MSSubClass', 'GrLivArea',
       '2ndFlrSF', 'BsmtQual', 'TotRmsAbvGrd', 'Fireplaces', 'HalfBath'],
      dtype='object')

In [16]:
print("There are {} numerical features with Skew > 0.6 :".format(high_skew.shape[0]))
skewness = pd.DataFrame({'Skew' :high_skew})
skewness

There are 19 numerical features with Skew > 0.6 :


Skew
MiscVal        21.947195
PoolArea       16.898328
LotArea        12.822431
LowQualFinSF   12.088761
3SsnPorch      11.376065
KitchenAbvGr    4.302254
EnclosedPorch   4.003891
ScreenPorch     3.946694
OpenPorchSF     2.535114
WoodDeckSF      1.842433
LotFrontage     1.645574
1stFlrSF        1.469604
MSSubClass      1.375457
GrLivArea       1.269358
2ndFlrSF        0.861675
BsmtQual        0.796302
TotRmsAbvGrd    0.758367
Fireplaces      0.733495
HalfBath        0.694566

To normalize the features with skew above 0.6 using the Yeo-Johnson transformation where, unlike the Box-Cox transformation, zeros can be utilized. These transformations use several values of transformer parameters and select the one that returns the best transformation is selected. 

In [17]:
yjt = YeoJohnsonTransformer()
yjt.fit(train_test[skew_index])
train_test[skew_index] = yjt.transform(train_test[skew_index])

In [18]:
skew_features = train_test[number_cols].apply(lambda x: skew(x)).sort_values(ascending=False)
high_skew = skew_features[skew_features > 0.6]
skew_index = high_skew.index
skew_index

Index(['PoolArea', '3SsnPorch', 'LowQualFinSF', 'MiscVal', 'ScreenPorch',
       'EnclosedPorch'],
      dtype='object')

In [19]:
print("There are {} numerical features with Skew > 0.6 :".format(high_skew.shape[0]))
skewness = pd.DataFrame({'Skew' :high_skew})
skewness

There are 6 numerical features with Skew > 0.6 :


Skew
PoolArea       14.884318
3SsnPorch       8.712332
LowQualFinSF    8.365937
MiscVal         5.037498
ScreenPorch     2.915215
EnclosedPorch   1.883152

It will be necessary to identify all the columns that have non-numeric object values and then convert them to numeric values. 

In [20]:
obj_cols = list(train_test.select_dtypes(['object']).columns)

In [21]:
for column in obj_cols:
     train_test[column] = pd.factorize(train_test[column], sort=True)[0]

To create some new columns that might compound the effects of the existing columns with higher impact on the xgb score. Used the get_score function with 'gain' as the importance type. This takes the average gain of the tree splits. 

In [22]:
train_test['QualCondSum'] = train_test['OverallQual'] + train_test['OverallCond']
train_test['RemodTime'] = train_test['YearRemodAdd'] - train_test['YearBuilt']
train_test['BsmtFinTypeSF1'] = train_test['BsmtFinType1'] * train_test['BsmtFinSF1']
train_test['TotalFlrSF'] = train_test['1stFlrSF'] + train_test['2ndFlrSF']
train_test['TotalFinSF'] = train_test['GrLivArea'] + train_test['BsmtFinSF1']
train_test['GarageCarArea'] = train_test['GarageArea'] * train_test['GarageCars']
train_test['TotalSF'] = train_test['1stFlrSF'] + train_test['2ndFlrSF'] + train_test['TotalBsmtSF']

To now eliminate the columns that have negative or zero influence on the xgb score. 

In [23]:
'''train_test.drop(['Utilities','Street','TotRmsAbvGrd','3SsnPorch','YrSold','Exterior2nd','LotConfig',
                              'HouseStyle','EnclosedPorch','WoodDeckSF','Foundation','RoofMatl','Electrical',
                              'GarageType','LotFrontage','SaleType','MoSold','BsmtExposure','1stFlrSF',
                              'BsmtFinSF1','Exterior1st','KitchenQual','TotalFlrSF'], axis=1, inplace=True)'''

To create a column with the log of the SalePrice to match the evaluation process in the contest. 

In [23]:
train_test['LogSalePrice'] = train_test['SalePrice'].apply(np.log)

WHY THESE FEATURES? HOW DOES IT WORK?

In [206]:
# Remove outliers
#train_test.drop(train_test[(train_test['OverallQual']<5) & (train_test['LogSalePrice']>200000)].index, inplace=True)
#train_test.drop(train_test[(train['GrLivArea']>4500) & (train_test['LogSalePrice']<300000)].index, inplace=True)
#train_test.reset_index(drop=True, inplace=True)

To separate the train_test dataset back into the train and test datasets, identify the independent and dependent columns, and create the validation split.

In [24]:
train = train_test[train_test['SalePrice'].notnull()].copy()
test = train_test[train_test['SalePrice'].isnull()].drop(['SalePrice','LogSalePrice'],axis=1)
X = train.drop(['SalePrice','LogSalePrice'],axis=1)
y = train.LogSalePrice

In [25]:
X,y = shuffle(X,y, random_state=42)
X = X.reset_index(drop=True)
y = y.reset_index(drop=True)

In [50]:
# Setup cross validation folds
kf = KFold(n_splits=12, random_state=42, shuffle=True)

In [35]:
cat_model = CatBoostRegressor()

#xgb_model = xgb.XGBRegressor()

'''xgb_model = xgb.XGBRegressor(learning_rate=0.01,
                       n_estimators=6000,
                       max_depth=4,
                       min_child_weight=0,
                       gamma=0.6,
                       subsample=0.7,
                       colsample_bytree=0.7,
                       objective='reg:linear',
                       nthread=-1,
                       scale_pos_weight=1,
                       seed=27,
                       reg_alpha=0.00006,
                       random_state=42)'''

xgb_model = xgb.XGBRegressor(reg_lambda=1.32754289013568, 
                    alpha=1.580513088436275, 
                    colsample_bytree=0.34112979113700337, 
                    subsample=0.49829211790557504, 
                    learning_rate= 0.04245317476432714, 
                    n_estimators= 1145,
                    max_depth= 6, 
                    min_child_weight= 6, 
                    num_parallel_tree= 1)


lr_model = LinearRegression()

br_model = BayesianRidge(compute_score=True)

lightgbm_model = LGBMRegressor(objective='regression', 
                       num_leaves=6,
                       learning_rate=0.01, 
                       n_estimators=7000,
                       max_bin=200, 
                       bagging_fraction=0.8,
                       bagging_freq=4, 
                       bagging_seed=8,
                       feature_fraction=0.2,
                       feature_fraction_seed=8,
                       min_sum_hessian_in_leaf = 11,
                       verbose=-1,
                       random_state=42)

svr_model = make_pipeline(RobustScaler(), SVR(C= 20, epsilon= 0.008, gamma=0.0003))

dtr_model = DecisionTreeRegressor()

rfr_model = RandomForestRegressor(n_estimators=1200,
                          max_depth=15,
                          min_samples_split=5,
                          min_samples_leaf=5,
                          max_features=None,
                          oob_score=True,
                          random_state=42)

gbr_model = GradientBoostingRegressor(n_estimators=6000,
                                learning_rate=0.01,
                                max_depth=4,
                                max_features='sqrt',
                                min_samples_leaf=15,
                                min_samples_split=10,
                                loss='huber',
                                random_state=42)

ridge_alphas = [1e-15, 1e-10, 1e-8, 9e-4, 7e-4, 5e-4, 3e-4, 1e-4, 1e-3, 5e-2, 1e-2, 0.1, 0.3, 1, 3, 5, 10, 15, 
                18, 20, 30, 50, 75, 100]
ridge_model = make_pipeline(RobustScaler(), RidgeCV(alphas=ridge_alphas, cv=kf))

In [51]:
def rmse_cv(model,X,y):
    rmse = np.sqrt(-cross_val_score(model, X, y, scoring="neg_mean_squared_error", cv=kf))
    return rmse

In [30]:
print(rmse_cv(xgb_model,X,y).mean())

0.12362008955374755


In [229]:
print(rmse_cv(cat_model,X,y).mean())

Learning rate set to 0.042871
0:	learn: 0.3917821	total: 4.72ms	remaining: 4.72s
1:	learn: 0.3817209	total: 8.51ms	remaining: 4.25s
2:	learn: 0.3715647	total: 12ms	remaining: 3.99s
3:	learn: 0.3617439	total: 15.8ms	remaining: 3.94s
4:	learn: 0.3518650	total: 19.4ms	remaining: 3.85s
5:	learn: 0.3424260	total: 22.6ms	remaining: 3.74s
6:	learn: 0.3335014	total: 26.1ms	remaining: 3.7s
7:	learn: 0.3254587	total: 29.1ms	remaining: 3.61s
8:	learn: 0.3174372	total: 32ms	remaining: 3.52s
9:	learn: 0.3095376	total: 34.5ms	remaining: 3.42s
10:	learn: 0.3015747	total: 37.3ms	remaining: 3.35s
11:	learn: 0.2945416	total: 40.3ms	remaining: 3.31s
12:	learn: 0.2871495	total: 43ms	remaining: 3.26s
13:	learn: 0.2803161	total: 45.6ms	remaining: 3.21s
14:	learn: 0.2739835	total: 48.1ms	remaining: 3.16s
15:	learn: 0.2682322	total: 50.8ms	remaining: 3.13s
16:	learn: 0.2621020	total: 53.5ms	remaining: 3.09s
17:	learn: 0.2572777	total: 56.8ms	remaining: 3.1s
18:	learn: 0.2517478	total: 59.9ms	remaining: 3.09s


205:	learn: 0.0929880	total: 539ms	remaining: 2.08s
206:	learn: 0.0928898	total: 542ms	remaining: 2.08s
207:	learn: 0.0927804	total: 545ms	remaining: 2.07s
208:	learn: 0.0926431	total: 547ms	remaining: 2.07s
209:	learn: 0.0924683	total: 550ms	remaining: 2.07s
210:	learn: 0.0922415	total: 552ms	remaining: 2.06s
211:	learn: 0.0920141	total: 555ms	remaining: 2.06s
212:	learn: 0.0918737	total: 558ms	remaining: 2.06s
213:	learn: 0.0917227	total: 561ms	remaining: 2.06s
214:	learn: 0.0915364	total: 563ms	remaining: 2.06s
215:	learn: 0.0913834	total: 566ms	remaining: 2.06s
216:	learn: 0.0912224	total: 570ms	remaining: 2.06s
217:	learn: 0.0911324	total: 572ms	remaining: 2.05s
218:	learn: 0.0910549	total: 575ms	remaining: 2.05s
219:	learn: 0.0909731	total: 577ms	remaining: 2.04s
220:	learn: 0.0908189	total: 579ms	remaining: 2.04s
221:	learn: 0.0906819	total: 581ms	remaining: 2.04s
222:	learn: 0.0905323	total: 584ms	remaining: 2.03s
223:	learn: 0.0902844	total: 586ms	remaining: 2.03s
224:	learn: 

381:	learn: 0.0718985	total: 987ms	remaining: 1.6s
382:	learn: 0.0718164	total: 993ms	remaining: 1.6s
383:	learn: 0.0717436	total: 998ms	remaining: 1.6s
384:	learn: 0.0716473	total: 1s	remaining: 1.6s
385:	learn: 0.0714960	total: 1.01s	remaining: 1.61s
386:	learn: 0.0713297	total: 1.02s	remaining: 1.61s
387:	learn: 0.0712407	total: 1.02s	remaining: 1.61s
388:	learn: 0.0711344	total: 1.03s	remaining: 1.61s
389:	learn: 0.0710769	total: 1.03s	remaining: 1.62s
390:	learn: 0.0710401	total: 1.04s	remaining: 1.62s
391:	learn: 0.0709695	total: 1.05s	remaining: 1.62s
392:	learn: 0.0709401	total: 1.05s	remaining: 1.63s
393:	learn: 0.0708393	total: 1.06s	remaining: 1.63s
394:	learn: 0.0707130	total: 1.06s	remaining: 1.63s
395:	learn: 0.0705941	total: 1.07s	remaining: 1.63s
396:	learn: 0.0705022	total: 1.07s	remaining: 1.63s
397:	learn: 0.0704045	total: 1.08s	remaining: 1.63s
398:	learn: 0.0702987	total: 1.08s	remaining: 1.63s
399:	learn: 0.0701636	total: 1.09s	remaining: 1.63s
400:	learn: 0.07010

568:	learn: 0.0575963	total: 1.57s	remaining: 1.19s
569:	learn: 0.0575183	total: 1.58s	remaining: 1.2s
570:	learn: 0.0574542	total: 1.59s	remaining: 1.19s
571:	learn: 0.0573886	total: 1.59s	remaining: 1.19s
572:	learn: 0.0573104	total: 1.59s	remaining: 1.19s
573:	learn: 0.0572616	total: 1.59s	remaining: 1.18s
574:	learn: 0.0571854	total: 1.59s	remaining: 1.18s
575:	learn: 0.0570806	total: 1.6s	remaining: 1.18s
576:	learn: 0.0570383	total: 1.6s	remaining: 1.17s
577:	learn: 0.0569311	total: 1.6s	remaining: 1.17s
578:	learn: 0.0568792	total: 1.6s	remaining: 1.17s
579:	learn: 0.0568377	total: 1.61s	remaining: 1.16s
580:	learn: 0.0567691	total: 1.61s	remaining: 1.16s
581:	learn: 0.0567544	total: 1.61s	remaining: 1.16s
582:	learn: 0.0566709	total: 1.61s	remaining: 1.16s
583:	learn: 0.0566055	total: 1.62s	remaining: 1.15s
584:	learn: 0.0565529	total: 1.62s	remaining: 1.15s
585:	learn: 0.0564500	total: 1.62s	remaining: 1.15s
586:	learn: 0.0563967	total: 1.62s	remaining: 1.14s
587:	learn: 0.056

771:	learn: 0.0469680	total: 2.08s	remaining: 613ms
772:	learn: 0.0469034	total: 2.08s	remaining: 611ms
773:	learn: 0.0468312	total: 2.08s	remaining: 608ms
774:	learn: 0.0467746	total: 2.08s	remaining: 605ms
775:	learn: 0.0467236	total: 2.09s	remaining: 603ms
776:	learn: 0.0466995	total: 2.09s	remaining: 600ms
777:	learn: 0.0466265	total: 2.09s	remaining: 597ms
778:	learn: 0.0466244	total: 2.1s	remaining: 595ms
779:	learn: 0.0465726	total: 2.1s	remaining: 592ms
780:	learn: 0.0464760	total: 2.1s	remaining: 589ms
781:	learn: 0.0464493	total: 2.1s	remaining: 586ms
782:	learn: 0.0464138	total: 2.1s	remaining: 584ms
783:	learn: 0.0463385	total: 2.11s	remaining: 581ms
784:	learn: 0.0462292	total: 2.11s	remaining: 578ms
785:	learn: 0.0461503	total: 2.11s	remaining: 575ms
786:	learn: 0.0461035	total: 2.12s	remaining: 572ms
787:	learn: 0.0460602	total: 2.12s	remaining: 570ms
788:	learn: 0.0460227	total: 2.12s	remaining: 567ms
789:	learn: 0.0459885	total: 2.12s	remaining: 564ms
790:	learn: 0.045

...

64:	learn: 0.1381660	total: 198ms	remaining: 2.84s
65:	learn: 0.1370433	total: 201ms	remaining: 2.85s
66:	learn: 0.1360721	total: 204ms	remaining: 2.84s
67:	learn: 0.1353262	total: 208ms	remaining: 2.84s
68:	learn: 0.1344246	total: 211ms	remaining: 2.85s
69:	learn: 0.1336427	total: 214ms	remaining: 2.85s
70:	learn: 0.1328530	total: 218ms	remaining: 2.85s
71:	learn: 0.1321779	total: 222ms	remaining: 2.86s
72:	learn: 0.1313206	total: 225ms	remaining: 2.86s
73:	learn: 0.1305060	total: 229ms	remaining: 2.86s
74:	learn: 0.1298137	total: 232ms	remaining: 2.86s
75:	learn: 0.1291751	total: 235ms	remaining: 2.85s
76:	learn: 0.1283872	total: 237ms	remaining: 2.85s
77:	learn: 0.1276582	total: 241ms	remaining: 2.84s
78:	learn: 0.1270469	total: 243ms	remaining: 2.84s
79:	learn: 0.1263886	total: 246ms	remaining: 2.83s
80:	learn: 0.1258275	total: 249ms	remaining: 2.83s
81:	learn: 0.1252862	total: 252ms	remaining: 2.82s
82:	learn: 0.1246613	total: 255ms	remaining: 2.82s
83:	learn: 0.1240198	total: 258

234:	learn: 0.0882143	total: 788ms	remaining: 2.56s
235:	learn: 0.0880506	total: 793ms	remaining: 2.57s
236:	learn: 0.0879163	total: 797ms	remaining: 2.56s
237:	learn: 0.0878337	total: 801ms	remaining: 2.56s
238:	learn: 0.0876725	total: 805ms	remaining: 2.56s
239:	learn: 0.0875686	total: 810ms	remaining: 2.56s
240:	learn: 0.0872935	total: 814ms	remaining: 2.56s
241:	learn: 0.0871767	total: 818ms	remaining: 2.56s
242:	learn: 0.0870856	total: 821ms	remaining: 2.56s
243:	learn: 0.0868337	total: 825ms	remaining: 2.56s
244:	learn: 0.0866719	total: 828ms	remaining: 2.55s
245:	learn: 0.0865370	total: 832ms	remaining: 2.55s
246:	learn: 0.0864268	total: 836ms	remaining: 2.55s
247:	learn: 0.0862843	total: 840ms	remaining: 2.55s
248:	learn: 0.0861534	total: 844ms	remaining: 2.54s
249:	learn: 0.0859481	total: 848ms	remaining: 2.54s
250:	learn: 0.0857669	total: 851ms	remaining: 2.54s
251:	learn: 0.0856811	total: 855ms	remaining: 2.54s
252:	learn: 0.0855206	total: 858ms	remaining: 2.53s
253:	learn: 

412:	learn: 0.0695239	total: 1.37s	remaining: 1.95s
413:	learn: 0.0694528	total: 1.38s	remaining: 1.95s
414:	learn: 0.0693676	total: 1.38s	remaining: 1.95s
415:	learn: 0.0692477	total: 1.38s	remaining: 1.94s
416:	learn: 0.0691446	total: 1.39s	remaining: 1.94s
417:	learn: 0.0690175	total: 1.39s	remaining: 1.94s
418:	learn: 0.0689134	total: 1.4s	remaining: 1.93s
419:	learn: 0.0688381	total: 1.4s	remaining: 1.93s
420:	learn: 0.0687179	total: 1.4s	remaining: 1.93s
421:	learn: 0.0685683	total: 1.4s	remaining: 1.92s
422:	learn: 0.0684710	total: 1.41s	remaining: 1.92s
423:	learn: 0.0684314	total: 1.41s	remaining: 1.92s
424:	learn: 0.0683133	total: 1.41s	remaining: 1.91s
425:	learn: 0.0682166	total: 1.42s	remaining: 1.91s
426:	learn: 0.0681616	total: 1.42s	remaining: 1.91s
427:	learn: 0.0680526	total: 1.42s	remaining: 1.9s
428:	learn: 0.0679661	total: 1.43s	remaining: 1.9s
429:	learn: 0.0679029	total: 1.43s	remaining: 1.89s
430:	learn: 0.0678009	total: 1.43s	remaining: 1.89s
431:	learn: 0.0677

622:	learn: 0.0545987	total: 2.15s	remaining: 1.3s
623:	learn: 0.0545446	total: 2.15s	remaining: 1.3s
624:	learn: 0.0544949	total: 2.16s	remaining: 1.29s
625:	learn: 0.0544299	total: 2.16s	remaining: 1.29s
626:	learn: 0.0543714	total: 2.16s	remaining: 1.29s
627:	learn: 0.0543173	total: 2.17s	remaining: 1.28s
628:	learn: 0.0542557	total: 2.17s	remaining: 1.28s
629:	learn: 0.0542130	total: 2.17s	remaining: 1.28s
630:	learn: 0.0542070	total: 2.18s	remaining: 1.27s
631:	learn: 0.0541444	total: 2.18s	remaining: 1.27s
632:	learn: 0.0540766	total: 2.19s	remaining: 1.27s
633:	learn: 0.0540549	total: 2.19s	remaining: 1.26s
634:	learn: 0.0539963	total: 2.19s	remaining: 1.26s
635:	learn: 0.0539173	total: 2.19s	remaining: 1.25s
636:	learn: 0.0538562	total: 2.2s	remaining: 1.25s
637:	learn: 0.0537813	total: 2.2s	remaining: 1.25s
638:	learn: 0.0537139	total: 2.2s	remaining: 1.24s
639:	learn: 0.0537106	total: 2.21s	remaining: 1.24s
640:	learn: 0.0536539	total: 2.21s	remaining: 1.24s
641:	learn: 0.053

815:	learn: 0.0447414	total: 2.73s	remaining: 617ms
816:	learn: 0.0447049	total: 2.74s	remaining: 613ms
817:	learn: 0.0446610	total: 2.74s	remaining: 610ms
818:	learn: 0.0446132	total: 2.75s	remaining: 607ms
819:	learn: 0.0445757	total: 2.75s	remaining: 603ms
820:	learn: 0.0445254	total: 2.75s	remaining: 600ms
821:	learn: 0.0445115	total: 2.76s	remaining: 597ms
822:	learn: 0.0444724	total: 2.76s	remaining: 594ms
823:	learn: 0.0444686	total: 2.76s	remaining: 590ms
824:	learn: 0.0444317	total: 2.77s	remaining: 587ms
825:	learn: 0.0443562	total: 2.77s	remaining: 583ms
826:	learn: 0.0443538	total: 2.77s	remaining: 580ms
827:	learn: 0.0443516	total: 2.77s	remaining: 576ms
828:	learn: 0.0443314	total: 2.78s	remaining: 573ms
829:	learn: 0.0443026	total: 2.78s	remaining: 570ms
830:	learn: 0.0442880	total: 2.78s	remaining: 566ms
831:	learn: 0.0442644	total: 2.79s	remaining: 563ms
832:	learn: 0.0442207	total: 2.79s	remaining: 559ms
833:	learn: 0.0441913	total: 2.79s	remaining: 556ms
834:	learn: 

In [37]:
model_names = ['CatBoostRegressor','XGBRegressor','LinearRegression','BayesianRidge','LGBMRegressor',
               'SVR','DecisionTreeRegressor','RandomForestRegressor','GradientBoostingRegressor','RidgeRegressor']

In [38]:
models = [cat_model,xgb_model,lr_model,br_model,lightgbm_model,svr_model,dtr_model,rfr_model,gbr_model,ridge_model]

In [39]:
score_rmse = []
for i in models:
    rmse = np.sqrt(-cross_val_score(i, X, y, scoring="neg_mean_squared_error", cv=kf))
    ave_rmse = np.mean(rmse)
    score_rmse.append(ave_rmse)

Learning rate set to 0.043115
0:	learn: 0.3895668	total: 156ms	remaining: 2m 36s
1:	learn: 0.3785587	total: 160ms	remaining: 1m 19s
2:	learn: 0.3680650	total: 163ms	remaining: 54.2s
3:	learn: 0.3580419	total: 166ms	remaining: 41.4s
4:	learn: 0.3496648	total: 170ms	remaining: 33.7s
5:	learn: 0.3407877	total: 173ms	remaining: 28.7s
6:	learn: 0.3322923	total: 177ms	remaining: 25.1s
7:	learn: 0.3234157	total: 181ms	remaining: 22.4s
8:	learn: 0.3153299	total: 185ms	remaining: 20.3s
9:	learn: 0.3070940	total: 188ms	remaining: 18.6s
10:	learn: 0.2995258	total: 192ms	remaining: 17.2s
11:	learn: 0.2925938	total: 196ms	remaining: 16.1s
12:	learn: 0.2860415	total: 199ms	remaining: 15.1s
13:	learn: 0.2795187	total: 203ms	remaining: 14.3s
14:	learn: 0.2729770	total: 206ms	remaining: 13.5s
15:	learn: 0.2676247	total: 210ms	remaining: 12.9s
16:	learn: 0.2615992	total: 214ms	remaining: 12.3s
17:	learn: 0.2560292	total: 217ms	remaining: 11.9s
18:	learn: 0.2502768	total: 221ms	remaining: 11.4s
19:	learn

174:	learn: 0.0977935	total: 787ms	remaining: 3.71s
175:	learn: 0.0976274	total: 796ms	remaining: 3.73s
176:	learn: 0.0974797	total: 804ms	remaining: 3.74s
177:	learn: 0.0973940	total: 812ms	remaining: 3.75s
178:	learn: 0.0972076	total: 821ms	remaining: 3.77s
179:	learn: 0.0969240	total: 827ms	remaining: 3.77s
180:	learn: 0.0967382	total: 835ms	remaining: 3.78s
181:	learn: 0.0965690	total: 842ms	remaining: 3.78s
182:	learn: 0.0963580	total: 848ms	remaining: 3.79s
183:	learn: 0.0962156	total: 857ms	remaining: 3.8s
184:	learn: 0.0960798	total: 871ms	remaining: 3.84s
185:	learn: 0.0959309	total: 878ms	remaining: 3.84s
186:	learn: 0.0957193	total: 885ms	remaining: 3.85s
187:	learn: 0.0956419	total: 891ms	remaining: 3.85s
188:	learn: 0.0954118	total: 896ms	remaining: 3.84s
189:	learn: 0.0952754	total: 903ms	remaining: 3.85s
190:	learn: 0.0951263	total: 909ms	remaining: 3.85s
191:	learn: 0.0948883	total: 916ms	remaining: 3.86s
192:	learn: 0.0947836	total: 922ms	remaining: 3.86s
193:	learn: 0

361:	learn: 0.0731349	total: 1.6s	remaining: 2.82s
362:	learn: 0.0731175	total: 1.6s	remaining: 2.81s
363:	learn: 0.0730040	total: 1.6s	remaining: 2.8s
364:	learn: 0.0728825	total: 1.61s	remaining: 2.79s
365:	learn: 0.0727773	total: 1.61s	remaining: 2.79s
366:	learn: 0.0726706	total: 1.61s	remaining: 2.78s
367:	learn: 0.0725993	total: 1.61s	remaining: 2.77s
368:	learn: 0.0725731	total: 1.62s	remaining: 2.77s
369:	learn: 0.0724892	total: 1.62s	remaining: 2.76s
370:	learn: 0.0723504	total: 1.63s	remaining: 2.75s
371:	learn: 0.0722247	total: 1.63s	remaining: 2.75s
372:	learn: 0.0721336	total: 1.63s	remaining: 2.74s
373:	learn: 0.0720259	total: 1.63s	remaining: 2.74s
374:	learn: 0.0719693	total: 1.64s	remaining: 2.73s
375:	learn: 0.0718745	total: 1.64s	remaining: 2.72s
376:	learn: 0.0717661	total: 1.64s	remaining: 2.72s
377:	learn: 0.0716424	total: 1.65s	remaining: 2.71s
378:	learn: 0.0716011	total: 1.65s	remaining: 2.7s
379:	learn: 0.0714442	total: 1.65s	remaining: 2.7s
380:	learn: 0.0714

548:	learn: 0.0576933	total: 2.18s	remaining: 1.79s
549:	learn: 0.0576598	total: 2.19s	remaining: 1.79s
550:	learn: 0.0575461	total: 2.19s	remaining: 1.78s
551:	learn: 0.0574420	total: 2.19s	remaining: 1.78s
552:	learn: 0.0573568	total: 2.2s	remaining: 1.78s
553:	learn: 0.0573129	total: 2.2s	remaining: 1.77s
554:	learn: 0.0571895	total: 2.2s	remaining: 1.77s
555:	learn: 0.0570758	total: 2.21s	remaining: 1.76s
556:	learn: 0.0570654	total: 2.21s	remaining: 1.76s
557:	learn: 0.0569456	total: 2.21s	remaining: 1.75s
558:	learn: 0.0568180	total: 2.22s	remaining: 1.75s
559:	learn: 0.0567092	total: 2.23s	remaining: 1.75s
560:	learn: 0.0566166	total: 2.23s	remaining: 1.74s
561:	learn: 0.0565875	total: 2.23s	remaining: 1.74s
562:	learn: 0.0565026	total: 2.24s	remaining: 1.74s
563:	learn: 0.0564907	total: 2.24s	remaining: 1.73s
564:	learn: 0.0563949	total: 2.24s	remaining: 1.73s
565:	learn: 0.0563166	total: 2.25s	remaining: 1.72s
566:	learn: 0.0562889	total: 2.25s	remaining: 1.72s
567:	learn: 0.0

750:	learn: 0.0448293	total: 2.96s	remaining: 982ms
751:	learn: 0.0447629	total: 2.97s	remaining: 978ms
752:	learn: 0.0446899	total: 2.97s	remaining: 974ms
753:	learn: 0.0446826	total: 2.97s	remaining: 970ms
754:	learn: 0.0446255	total: 2.98s	remaining: 966ms
755:	learn: 0.0445562	total: 2.98s	remaining: 963ms
756:	learn: 0.0445466	total: 2.99s	remaining: 959ms
757:	learn: 0.0444928	total: 2.99s	remaining: 955ms
758:	learn: 0.0444071	total: 2.99s	remaining: 950ms
759:	learn: 0.0443384	total: 3s	remaining: 946ms
760:	learn: 0.0442797	total: 3s	remaining: 942ms
761:	learn: 0.0442084	total: 3s	remaining: 938ms
762:	learn: 0.0441774	total: 3.01s	remaining: 934ms
763:	learn: 0.0441058	total: 3.01s	remaining: 930ms
764:	learn: 0.0440591	total: 3.01s	remaining: 926ms
765:	learn: 0.0440094	total: 3.02s	remaining: 921ms
766:	learn: 0.0439413	total: 3.02s	remaining: 917ms
767:	learn: 0.0439182	total: 3.02s	remaining: 913ms
768:	learn: 0.0438242	total: 3.03s	remaining: 909ms
769:	learn: 0.0437861

...

[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] featu

Ill-conditioned matrix (rcond=2.67797e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.63251e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.68079e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.5922e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.66981e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.60472e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.63117e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.59342e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.64011e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.68158e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.58916e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.60986e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.54807e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.67007e-17): result may not be acc

Ill-conditioned matrix (rcond=2.66633e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.56703e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.45743e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.53295e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.53188e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.54367e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.53848e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.66295e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.47859e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.53357e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.6233e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.57448e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.60487e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.51769e-17): result may not be acc

Ill-conditioned matrix (rcond=2.87601e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.78803e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.83078e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.82901e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.67621e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.90985e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.64987e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.70416e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.66996e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.89326e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.6437e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.87596e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.76004e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.7221e-17): result may not be accu

Ill-conditioned matrix (rcond=5.98448e-21): result may not be accurate.
Ill-conditioned matrix (rcond=2.5165e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.42346e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.45374e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.44801e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.47223e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4915e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.52329e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.50171e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4687e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.47076e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.46747e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.57816e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.36213e-17): result may not be accur

In [40]:
model_scores = list(zip(model_names, score_rmse))

In [111]:
model_scores

[('CatBoostRegressor', 0.12110237674244963),
 ('XGBRegressor', 0.12398912144748252),
 ('LinearRegression', 0.13634490032529228),
 ('BayesianRidge', 0.1329249106338829),
 ('LGBMRegressor', 0.12389763773146073),
 ('SVR', 0.13425907290957856),
 ('DecisionTreeRegressor', 0.200078580127339),
 ('RandomForestRegressor', 0.14140317161332885),
 ('GradientBoostingRegressor', 0.12138213034855315),
 ('RidgeRegressor', 0.13144439888498063)]

In [240]:
#model_scores

[('CatBoostRegressor', 0.12203936434447392),
 ('XGBRegressor', 0.13462151511641332),
 ('LinearRegression', 0.13356662846280187),
 ('BayesianRidge', 0.1328006238708588),
 ('LGBMRegressor', 0.1245974683346716),
 ('SVR', 0.13475960391331226),
 ('DecisionTreeRegressor', 0.20203422926722994),
 ('RandomForestRegressor', 0.14092845972196566),
 ('GradientBoostingRegressor', 0.12302711142621658),
 ('RidgeRegressor', 0.13178872115356863)]

In [31]:
# Baseline scores
#model_scores

[('CatBoostRegressor', 0.11411205350616899),
 ('XGBRegressor', 0.13748288476654888),
 ('LinearRegression', 0.11969691765411448),
 ('BayesianRidge', 0.12061212544953019),
 ('LGBMRegressor', 0.11915209696117295),
 ('SVR', 0.1246562847252383),
 ('DecisionTreeRegressor', 0.20302051061417217),
 ('RandomForestRegressor', 0.13853112867269568),
 ('GradientBoostingRegressor', 0.11615172234950873),
 ('RidgeRegressor', 0.11967179571435715)]

In [32]:
# With default parameters
#model_scores

[('CatBoostRegressor', 0.11411205350616899),
 ('XGBRegressor', 0.13698185547470643),
 ('LinearRegression', 0.11969691765411448),
 ('BayesianRidge', 0.12061212544953019),
 ('LGBMRegressor', 0.1265171429674531),
 ('SVR', 0.2384458189370885),
 ('DecisionTreeRegressor', 0.20798226180188817),
 ('RandomForestRegressor', 0.13563910253987557),
 ('GradientBoostingRegressor', 0.12427935641474476)]

From 0.03 model: LightGBM: 0.1164, XGBoost: 0.1362, SVR: 0.1094, Ridge: 0.1101, RandomForest: 0.1366, GBR: 0.1121, StackGen: 0.1125, Blended: 0.0744

In [54]:
# Stack up all the models above except CatBoost, optimized using linear regressor
stack_gen = StackingCVRegressor(regressors=(xgb_model,lr_model,br_model,lightgbm_model,svr_model,
                                            dtr_model,rfr_model,gbr_model,ridge_model),
                                meta_regressor=lr_model,
                                #meta_regressor=xgboost,
                                #random_state=42
                                use_features_in_secondary=True)

In [53]:
print(rmse_cv(stack_gen,np.array(X),np.array(y)).mean())

Learning rate set to 0.041383
0:	learn: 0.3937849	total: 4.3ms	remaining: 4.3s
1:	learn: 0.3839107	total: 8.24ms	remaining: 4.11s
2:	learn: 0.3742651	total: 12.3ms	remaining: 4.1s
3:	learn: 0.3650626	total: 15.6ms	remaining: 3.87s
4:	learn: 0.3555727	total: 19.3ms	remaining: 3.84s
5:	learn: 0.3464052	total: 22.6ms	remaining: 3.74s
6:	learn: 0.3380641	total: 26.7ms	remaining: 3.79s
7:	learn: 0.3301466	total: 29.9ms	remaining: 3.7s
8:	learn: 0.3224899	total: 33ms	remaining: 3.63s
9:	learn: 0.3143818	total: 35.9ms	remaining: 3.55s
10:	learn: 0.3071804	total: 38.7ms	remaining: 3.48s
11:	learn: 0.3000036	total: 42.3ms	remaining: 3.48s
12:	learn: 0.2932662	total: 46ms	remaining: 3.49s
13:	learn: 0.2868896	total: 49.4ms	remaining: 3.48s
14:	learn: 0.2805879	total: 53.3ms	remaining: 3.5s
15:	learn: 0.2746803	total: 56.5ms	remaining: 3.47s
16:	learn: 0.2686769	total: 59.7ms	remaining: 3.45s
17:	learn: 0.2630839	total: 62.8ms	remaining: 3.43s
18:	learn: 0.2575181	total: 65.7ms	remaining: 3.39s
1

196:	learn: 0.0945652	total: 592ms	remaining: 2.41s
197:	learn: 0.0942849	total: 596ms	remaining: 2.41s
198:	learn: 0.0941103	total: 599ms	remaining: 2.41s
199:	learn: 0.0939645	total: 602ms	remaining: 2.41s
200:	learn: 0.0938005	total: 605ms	remaining: 2.4s
201:	learn: 0.0935091	total: 608ms	remaining: 2.4s
202:	learn: 0.0932174	total: 612ms	remaining: 2.4s
203:	learn: 0.0930578	total: 615ms	remaining: 2.4s
204:	learn: 0.0928712	total: 618ms	remaining: 2.4s
205:	learn: 0.0927324	total: 622ms	remaining: 2.4s
206:	learn: 0.0925615	total: 626ms	remaining: 2.4s
207:	learn: 0.0923742	total: 629ms	remaining: 2.39s
208:	learn: 0.0921635	total: 631ms	remaining: 2.39s
209:	learn: 0.0919762	total: 634ms	remaining: 2.38s
210:	learn: 0.0917908	total: 637ms	remaining: 2.38s
211:	learn: 0.0915936	total: 639ms	remaining: 2.38s
212:	learn: 0.0914623	total: 642ms	remaining: 2.37s
213:	learn: 0.0912644	total: 645ms	remaining: 2.37s
214:	learn: 0.0910774	total: 648ms	remaining: 2.36s
215:	learn: 0.09098

400:	learn: 0.0642667	total: 1.18s	remaining: 1.76s
401:	learn: 0.0642465	total: 1.18s	remaining: 1.76s
402:	learn: 0.0641184	total: 1.19s	remaining: 1.76s
403:	learn: 0.0640969	total: 1.19s	remaining: 1.75s
404:	learn: 0.0640758	total: 1.19s	remaining: 1.75s
405:	learn: 0.0639406	total: 1.19s	remaining: 1.75s
406:	learn: 0.0638265	total: 1.2s	remaining: 1.75s
407:	learn: 0.0636574	total: 1.21s	remaining: 1.76s
408:	learn: 0.0635292	total: 1.21s	remaining: 1.75s
409:	learn: 0.0634266	total: 1.22s	remaining: 1.75s
410:	learn: 0.0633186	total: 1.22s	remaining: 1.75s
411:	learn: 0.0632316	total: 1.23s	remaining: 1.75s
412:	learn: 0.0632114	total: 1.23s	remaining: 1.75s
413:	learn: 0.0631133	total: 1.23s	remaining: 1.74s
414:	learn: 0.0630051	total: 1.23s	remaining: 1.74s
415:	learn: 0.0628597	total: 1.24s	remaining: 1.74s
416:	learn: 0.0627679	total: 1.24s	remaining: 1.73s
417:	learn: 0.0626259	total: 1.24s	remaining: 1.73s
418:	learn: 0.0624975	total: 1.25s	remaining: 1.73s
419:	learn: 0

566:	learn: 0.0506057	total: 1.78s	remaining: 1.36s
567:	learn: 0.0504836	total: 1.78s	remaining: 1.36s
568:	learn: 0.0504104	total: 1.79s	remaining: 1.35s
569:	learn: 0.0503236	total: 1.79s	remaining: 1.35s
570:	learn: 0.0502507	total: 1.8s	remaining: 1.35s
571:	learn: 0.0501641	total: 1.8s	remaining: 1.35s
572:	learn: 0.0500975	total: 1.81s	remaining: 1.35s
573:	learn: 0.0500391	total: 1.81s	remaining: 1.34s
574:	learn: 0.0499586	total: 1.81s	remaining: 1.34s
575:	learn: 0.0498815	total: 1.82s	remaining: 1.34s
576:	learn: 0.0497978	total: 1.82s	remaining: 1.33s
577:	learn: 0.0497110	total: 1.82s	remaining: 1.33s
578:	learn: 0.0496355	total: 1.82s	remaining: 1.33s
579:	learn: 0.0495715	total: 1.83s	remaining: 1.32s
580:	learn: 0.0494614	total: 1.83s	remaining: 1.32s
581:	learn: 0.0493642	total: 1.83s	remaining: 1.32s
582:	learn: 0.0492806	total: 1.84s	remaining: 1.31s
583:	learn: 0.0492184	total: 1.84s	remaining: 1.31s
584:	learn: 0.0491155	total: 1.84s	remaining: 1.31s
585:	learn: 0.

738:	learn: 0.0393194	total: 2.38s	remaining: 841ms
739:	learn: 0.0393122	total: 2.38s	remaining: 838ms
740:	learn: 0.0392592	total: 2.39s	remaining: 835ms
741:	learn: 0.0392286	total: 2.39s	remaining: 832ms
742:	learn: 0.0391342	total: 2.4s	remaining: 830ms
743:	learn: 0.0390444	total: 2.4s	remaining: 827ms
744:	learn: 0.0389770	total: 2.41s	remaining: 824ms
745:	learn: 0.0389401	total: 2.41s	remaining: 821ms
746:	learn: 0.0388820	total: 2.42s	remaining: 818ms
747:	learn: 0.0388377	total: 2.42s	remaining: 815ms
748:	learn: 0.0387866	total: 2.42s	remaining: 812ms
749:	learn: 0.0387377	total: 2.43s	remaining: 810ms
750:	learn: 0.0386734	total: 2.43s	remaining: 807ms
751:	learn: 0.0386166	total: 2.44s	remaining: 804ms
752:	learn: 0.0385345	total: 2.44s	remaining: 801ms
753:	learn: 0.0384824	total: 2.45s	remaining: 798ms
754:	learn: 0.0384431	total: 2.45s	remaining: 795ms
755:	learn: 0.0383885	total: 2.45s	remaining: 792ms
756:	learn: 0.0382995	total: 2.46s	remaining: 789ms
757:	learn: 0.

...

722:	learn: 0.0450794	total: 4.03s	remaining: 1.54s
723:	learn: 0.0450155	total: 4.04s	remaining: 1.54s
724:	learn: 0.0450104	total: 4.04s	remaining: 1.53s
725:	learn: 0.0449604	total: 4.05s	remaining: 1.53s
726:	learn: 0.0449118	total: 4.05s	remaining: 1.52s
727:	learn: 0.0448604	total: 4.06s	remaining: 1.52s
728:	learn: 0.0448019	total: 4.07s	remaining: 1.51s
729:	learn: 0.0447733	total: 4.07s	remaining: 1.5s
730:	learn: 0.0447191	total: 4.08s	remaining: 1.5s
731:	learn: 0.0447069	total: 4.08s	remaining: 1.49s
732:	learn: 0.0446873	total: 4.09s	remaining: 1.49s
733:	learn: 0.0446140	total: 4.09s	remaining: 1.48s
734:	learn: 0.0445056	total: 4.1s	remaining: 1.48s
735:	learn: 0.0444356	total: 4.11s	remaining: 1.47s
736:	learn: 0.0443715	total: 4.11s	remaining: 1.47s
737:	learn: 0.0443254	total: 4.12s	remaining: 1.46s
738:	learn: 0.0442680	total: 4.12s	remaining: 1.46s
739:	learn: 0.0442066	total: 4.13s	remaining: 1.45s
740:	learn: 0.0441267	total: 4.13s	remaining: 1.44s
741:	learn: 0.0

908:	learn: 0.0368047	total: 5.05s	remaining: 506ms
909:	learn: 0.0367625	total: 5.06s	remaining: 500ms
910:	learn: 0.0366950	total: 5.06s	remaining: 495ms
911:	learn: 0.0366727	total: 5.07s	remaining: 489ms
912:	learn: 0.0366390	total: 5.07s	remaining: 484ms
913:	learn: 0.0365943	total: 5.08s	remaining: 478ms
914:	learn: 0.0365472	total: 5.08s	remaining: 472ms
915:	learn: 0.0365232	total: 5.09s	remaining: 467ms
916:	learn: 0.0364892	total: 5.1s	remaining: 461ms
917:	learn: 0.0364283	total: 5.1s	remaining: 456ms
918:	learn: 0.0363897	total: 5.11s	remaining: 450ms
919:	learn: 0.0363564	total: 5.11s	remaining: 445ms
920:	learn: 0.0362981	total: 5.12s	remaining: 439ms
921:	learn: 0.0362954	total: 5.12s	remaining: 434ms
922:	learn: 0.0362622	total: 5.13s	remaining: 428ms
923:	learn: 0.0362406	total: 5.13s	remaining: 422ms
924:	learn: 0.0361776	total: 5.14s	remaining: 417ms
925:	learn: 0.0361456	total: 5.14s	remaining: 411ms
926:	learn: 0.0361285	total: 5.15s	remaining: 406ms
927:	learn: 0.

Ill-conditioned matrix (rcond=1.87517e-20): result may not be accurate.
Ill-conditioned matrix (rcond=2.59195e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.72149e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.68039e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.63663e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.72664e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.74676e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.58685e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.69773e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.70132e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.76788e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.57382e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.71139e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.62165e-17): result may not be ac

nan



3 fits failed out of a total of 12.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
3 fits failed with the following error:
Traceback (most recent call last):
  File "C:\Users\tompe\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 680, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\tompe\anaconda3\lib\site-packages\mlxtend\regressor\stacking_cv_regression.py", line 215, in fit
    [
  File "C:\Users\tompe\anaconda3\lib\site-packages\mlxtend\regressor\stacking_cv_regression.py", line 216, in <listcomp>
    cross_val_predict(
  File "C:\Users\tompe\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 962, in cross_val_predict
    predictions = parallel(
  

In [55]:
cat_model_all_data = cat_model.fit(X,y)
xgb_model_all_data = xgb_model.fit(X,y)
lr_model_all_data = lr_model.fit(X,y)
br_model_all_data = br_model.fit(X,y)
lightgbm_model_all_data = lightgbm_model.fit(X,y)
svr_model_all_data = svr_model.fit(X,y)
dtr_model_all_data = dtr_model.fit(X,y)
rfr_model_all_data = rfr_model.fit(X,y)
gbr_model_all_data = gbr_model.fit(X,y)
ridge_model_all_data = ridge_model.fit(X,y)

Learning rate set to 0.043466
0:	learn: 0.3887653	total: 4.7ms	remaining: 4.7s
1:	learn: 0.3780724	total: 8.78ms	remaining: 4.38s
2:	learn: 0.3673789	total: 13.1ms	remaining: 4.37s
3:	learn: 0.3579527	total: 18.6ms	remaining: 4.62s
4:	learn: 0.3481907	total: 22.7ms	remaining: 4.52s
5:	learn: 0.3393072	total: 26.5ms	remaining: 4.4s
6:	learn: 0.3304085	total: 29.9ms	remaining: 4.24s
7:	learn: 0.3221058	total: 34ms	remaining: 4.22s
8:	learn: 0.3140380	total: 38.1ms	remaining: 4.2s
9:	learn: 0.3057983	total: 42.2ms	remaining: 4.17s
10:	learn: 0.2982468	total: 46.1ms	remaining: 4.15s
11:	learn: 0.2914473	total: 50.6ms	remaining: 4.17s
12:	learn: 0.2839797	total: 55.1ms	remaining: 4.18s
13:	learn: 0.2773849	total: 58.9ms	remaining: 4.15s
14:	learn: 0.2710109	total: 62.6ms	remaining: 4.11s
15:	learn: 0.2650521	total: 67ms	remaining: 4.12s
16:	learn: 0.2590965	total: 70.8ms	remaining: 4.09s
17:	learn: 0.2532364	total: 74.2ms	remaining: 4.04s
18:	learn: 0.2479219	total: 77.2ms	remaining: 3.99s


176:	learn: 0.0969976	total: 584ms	remaining: 2.71s
177:	learn: 0.0968478	total: 588ms	remaining: 2.71s
178:	learn: 0.0966848	total: 591ms	remaining: 2.71s
179:	learn: 0.0964338	total: 595ms	remaining: 2.71s
180:	learn: 0.0963382	total: 599ms	remaining: 2.71s
181:	learn: 0.0961520	total: 604ms	remaining: 2.71s
182:	learn: 0.0958941	total: 608ms	remaining: 2.71s
183:	learn: 0.0956642	total: 611ms	remaining: 2.71s
184:	learn: 0.0955183	total: 615ms	remaining: 2.71s
185:	learn: 0.0953026	total: 618ms	remaining: 2.71s
186:	learn: 0.0950748	total: 622ms	remaining: 2.7s
187:	learn: 0.0949328	total: 625ms	remaining: 2.7s
188:	learn: 0.0948016	total: 628ms	remaining: 2.69s
189:	learn: 0.0946133	total: 631ms	remaining: 2.69s
190:	learn: 0.0944325	total: 635ms	remaining: 2.69s
191:	learn: 0.0942609	total: 638ms	remaining: 2.69s
192:	learn: 0.0941002	total: 641ms	remaining: 2.68s
193:	learn: 0.0939228	total: 645ms	remaining: 2.68s
194:	learn: 0.0938257	total: 648ms	remaining: 2.67s
195:	learn: 0.

355:	learn: 0.0733635	total: 1.19s	remaining: 2.15s
356:	learn: 0.0732487	total: 1.19s	remaining: 2.15s
357:	learn: 0.0732074	total: 1.2s	remaining: 2.15s
358:	learn: 0.0731228	total: 1.2s	remaining: 2.14s
359:	learn: 0.0730911	total: 1.2s	remaining: 2.14s
360:	learn: 0.0729476	total: 1.21s	remaining: 2.14s
361:	learn: 0.0729295	total: 1.21s	remaining: 2.14s
362:	learn: 0.0728222	total: 1.22s	remaining: 2.13s
363:	learn: 0.0727184	total: 1.22s	remaining: 2.13s
364:	learn: 0.0726404	total: 1.23s	remaining: 2.13s
365:	learn: 0.0724601	total: 1.23s	remaining: 2.13s
366:	learn: 0.0724472	total: 1.23s	remaining: 2.13s
367:	learn: 0.0723212	total: 1.24s	remaining: 2.12s
368:	learn: 0.0722503	total: 1.24s	remaining: 2.12s
369:	learn: 0.0721492	total: 1.25s	remaining: 2.12s
370:	learn: 0.0720603	total: 1.25s	remaining: 2.12s
371:	learn: 0.0719921	total: 1.25s	remaining: 2.11s
372:	learn: 0.0718885	total: 1.26s	remaining: 2.11s
373:	learn: 0.0717513	total: 1.26s	remaining: 2.11s
374:	learn: 0.0

514:	learn: 0.0599386	total: 1.98s	remaining: 1.87s
515:	learn: 0.0598145	total: 1.99s	remaining: 1.87s
516:	learn: 0.0597406	total: 1.99s	remaining: 1.86s
517:	learn: 0.0596700	total: 2s	remaining: 1.86s
518:	learn: 0.0595641	total: 2.01s	remaining: 1.86s
519:	learn: 0.0594744	total: 2.02s	remaining: 1.86s
520:	learn: 0.0594201	total: 2.02s	remaining: 1.86s
521:	learn: 0.0593789	total: 2.03s	remaining: 1.86s
522:	learn: 0.0592645	total: 2.03s	remaining: 1.85s
523:	learn: 0.0592053	total: 2.04s	remaining: 1.85s
524:	learn: 0.0591459	total: 2.04s	remaining: 1.84s
525:	learn: 0.0590634	total: 2.04s	remaining: 1.84s
526:	learn: 0.0589499	total: 2.05s	remaining: 1.84s
527:	learn: 0.0588988	total: 2.05s	remaining: 1.83s
528:	learn: 0.0588042	total: 2.06s	remaining: 1.83s
529:	learn: 0.0587467	total: 2.06s	remaining: 1.83s
530:	learn: 0.0587047	total: 2.06s	remaining: 1.82s
531:	learn: 0.0586260	total: 2.07s	remaining: 1.82s
532:	learn: 0.0585538	total: 2.07s	remaining: 1.81s
533:	learn: 0.0

703:	learn: 0.0476254	total: 2.76s	remaining: 1.16s
704:	learn: 0.0476067	total: 2.77s	remaining: 1.16s
705:	learn: 0.0475616	total: 2.77s	remaining: 1.15s
706:	learn: 0.0475080	total: 2.77s	remaining: 1.15s
707:	learn: 0.0474734	total: 2.78s	remaining: 1.15s
708:	learn: 0.0474319	total: 2.78s	remaining: 1.14s
709:	learn: 0.0473637	total: 2.79s	remaining: 1.14s
710:	learn: 0.0472990	total: 2.79s	remaining: 1.14s
711:	learn: 0.0472579	total: 2.8s	remaining: 1.13s
712:	learn: 0.0472104	total: 2.8s	remaining: 1.13s
713:	learn: 0.0471541	total: 2.81s	remaining: 1.12s
714:	learn: 0.0470919	total: 2.81s	remaining: 1.12s
715:	learn: 0.0470466	total: 2.81s	remaining: 1.12s
716:	learn: 0.0469591	total: 2.82s	remaining: 1.11s
717:	learn: 0.0469290	total: 2.82s	remaining: 1.11s
718:	learn: 0.0468685	total: 2.83s	remaining: 1.1s
719:	learn: 0.0468111	total: 2.83s	remaining: 1.1s
720:	learn: 0.0468055	total: 2.83s	remaining: 1.1s
721:	learn: 0.0467257	total: 2.84s	remaining: 1.09s
722:	learn: 0.046

880:	learn: 0.0399790	total: 3.54s	remaining: 479ms
881:	learn: 0.0399491	total: 3.55s	remaining: 475ms
882:	learn: 0.0399037	total: 3.55s	remaining: 471ms
883:	learn: 0.0398555	total: 3.56s	remaining: 467ms
884:	learn: 0.0397958	total: 3.56s	remaining: 463ms
885:	learn: 0.0397669	total: 3.56s	remaining: 459ms
886:	learn: 0.0397625	total: 3.57s	remaining: 455ms
887:	learn: 0.0397323	total: 3.57s	remaining: 451ms
888:	learn: 0.0397256	total: 3.58s	remaining: 447ms
889:	learn: 0.0396905	total: 3.58s	remaining: 443ms
890:	learn: 0.0396486	total: 3.59s	remaining: 439ms
891:	learn: 0.0396447	total: 3.59s	remaining: 435ms
892:	learn: 0.0395761	total: 3.59s	remaining: 431ms
893:	learn: 0.0395375	total: 3.6s	remaining: 427ms
894:	learn: 0.0394949	total: 3.6s	remaining: 423ms
895:	learn: 0.0394733	total: 3.61s	remaining: 419ms
896:	learn: 0.0394369	total: 3.61s	remaining: 415ms
897:	learn: 0.0394068	total: 3.61s	remaining: 411ms
898:	learn: 0.0393265	total: 3.62s	remaining: 407ms
899:	learn: 0.

Ill-conditioned matrix (rcond=2.48448e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.50172e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.42246e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.43932e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.42259e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4328e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.41798e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.46857e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.48919e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.51992e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4273e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.60087e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.6473e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.47115e-17): result may not be accur

In [56]:
stack_gen_model = stack_gen.fit(np.array(X), np.array(y))

[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] featu

Ill-conditioned matrix (rcond=4.05196e-22): result may not be accurate.
Ill-conditioned matrix (rcond=3.3531e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.26009e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.18901e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.02388e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.12423e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.18655e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.32164e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.03497e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.31882e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.11816e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.20671e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.13423e-17): result may not be accurate.
Ill-conditioned matrix (rcond=3.10457e-17): result may not be acc

[LightGBM] [Warning] feature_fraction is set=0.2, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.2
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=11, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=11
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4


Ill-conditioned matrix (rcond=2.48448e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.50172e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.42246e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.43932e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.42259e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4328e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.41798e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.46857e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.48919e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.51992e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.4273e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.60087e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.6473e-17): result may not be accurate.
Ill-conditioned matrix (rcond=2.47115e-17): result may not be accur

In [57]:
# Blend models in order to make the final predictions more robust to overfitting
def blended_predictions(X):
    return ((0.1 * ridge_model_all_data.predict(X)) + \
            (0.1 * svr_model_all_data.predict(X)) + \
            (0.1 * cat_model_all_data.predict(X)) + \
            (0.1 * gbr_model_all_data.predict(X)) + \
            (0.1 * xgb_model_all_data.predict(X)) + \
            (0.1 * lightgbm_model_all_data.predict(X)) + \
            (0.05 * rfr_model_all_data.predict(X)) + \
            (0.35 * stack_gen_model.predict(np.array(X))))

In [58]:
def rmsle(y, y_pred):
    return np.sqrt(mean_squared_error(y, y_pred))

In [59]:
# Get final precitions from the blended model
blended_score = rmsle(y, blended_predictions(X))
#scores['blended'] = (blended_score, 0)
print('RMLSE score on train data:')
print(blended_score)

RMLSE score on train data:
0.08088152290729315


In [60]:
print(rmse_cv(blended_predictions,X,y).mean())

TypeError: estimator should be an estimator implementing 'fit' method, <function blended_predictions at 0x000001F4B5F3DDC0> was passed

In [45]:
submit = test[['Id']]
submit = submit.reset_index(drop=True)

In [30]:
xgb_model.fit(X,y)

XGBRegressor(alpha=1.580513088436275, base_score=None, booster=None,
             callbacks=None, colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.34112979113700337, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.04245317476432714,
             max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=6, max_leaves=None,
             min_child_weight=6, missing=nan, monotone_constraints=None,
             n_estimators=1145, n_jobs=None, num_parallel_tree=1,
             predictor=None, ...)

In [46]:
cat_model.fit(X,y)

Learning rate set to 0.043466
0:	learn: 0.3887653	total: 4.96ms	remaining: 4.96s
1:	learn: 0.3780724	total: 8.95ms	remaining: 4.47s
2:	learn: 0.3673789	total: 13.2ms	remaining: 4.38s
3:	learn: 0.3579527	total: 18.5ms	remaining: 4.6s
4:	learn: 0.3481907	total: 22.9ms	remaining: 4.56s
5:	learn: 0.3393072	total: 26.6ms	remaining: 4.4s
6:	learn: 0.3304085	total: 31.6ms	remaining: 4.49s
7:	learn: 0.3221058	total: 34.9ms	remaining: 4.33s
8:	learn: 0.3140380	total: 38.2ms	remaining: 4.21s
9:	learn: 0.3057983	total: 41.4ms	remaining: 4.09s
10:	learn: 0.2982468	total: 46ms	remaining: 4.13s
11:	learn: 0.2914473	total: 50.4ms	remaining: 4.15s
12:	learn: 0.2839797	total: 53.7ms	remaining: 4.07s
13:	learn: 0.2773849	total: 57.2ms	remaining: 4.03s
14:	learn: 0.2710109	total: 61.4ms	remaining: 4.03s
15:	learn: 0.2650521	total: 64.7ms	remaining: 3.98s
16:	learn: 0.2590965	total: 67.8ms	remaining: 3.92s
17:	learn: 0.2532364	total: 70.9ms	remaining: 3.87s
18:	learn: 0.2479219	total: 74ms	remaining: 3.82

168:	learn: 0.0987240	total: 586ms	remaining: 2.88s
169:	learn: 0.0985303	total: 589ms	remaining: 2.88s
170:	learn: 0.0982979	total: 592ms	remaining: 2.87s
171:	learn: 0.0981214	total: 596ms	remaining: 2.87s
172:	learn: 0.0979164	total: 599ms	remaining: 2.86s
173:	learn: 0.0977185	total: 602ms	remaining: 2.86s
174:	learn: 0.0975204	total: 606ms	remaining: 2.86s
175:	learn: 0.0973234	total: 610ms	remaining: 2.85s
176:	learn: 0.0969976	total: 612ms	remaining: 2.85s
177:	learn: 0.0968478	total: 616ms	remaining: 2.84s
178:	learn: 0.0966848	total: 619ms	remaining: 2.84s
179:	learn: 0.0964338	total: 622ms	remaining: 2.83s
180:	learn: 0.0963382	total: 624ms	remaining: 2.83s
181:	learn: 0.0961520	total: 627ms	remaining: 2.82s
182:	learn: 0.0958941	total: 631ms	remaining: 2.81s
183:	learn: 0.0956642	total: 633ms	remaining: 2.81s
184:	learn: 0.0955183	total: 636ms	remaining: 2.8s
185:	learn: 0.0953026	total: 639ms	remaining: 2.8s
186:	learn: 0.0950748	total: 642ms	remaining: 2.79s
187:	learn: 0.

327:	learn: 0.0762601	total: 1.19s	remaining: 2.44s
328:	learn: 0.0760981	total: 1.2s	remaining: 2.44s
329:	learn: 0.0759454	total: 1.2s	remaining: 2.44s
330:	learn: 0.0758319	total: 1.21s	remaining: 2.44s
331:	learn: 0.0757343	total: 1.21s	remaining: 2.44s
332:	learn: 0.0756582	total: 1.22s	remaining: 2.44s
333:	learn: 0.0755865	total: 1.22s	remaining: 2.44s
334:	learn: 0.0755447	total: 1.23s	remaining: 2.43s
335:	learn: 0.0754885	total: 1.23s	remaining: 2.43s
336:	learn: 0.0752967	total: 1.24s	remaining: 2.43s
337:	learn: 0.0751396	total: 1.24s	remaining: 2.43s
338:	learn: 0.0749963	total: 1.24s	remaining: 2.42s
339:	learn: 0.0749253	total: 1.25s	remaining: 2.42s
340:	learn: 0.0748140	total: 1.25s	remaining: 2.42s
341:	learn: 0.0747137	total: 1.25s	remaining: 2.42s
342:	learn: 0.0745713	total: 1.26s	remaining: 2.41s
343:	learn: 0.0745527	total: 1.26s	remaining: 2.41s
344:	learn: 0.0744600	total: 1.27s	remaining: 2.4s
345:	learn: 0.0743440	total: 1.27s	remaining: 2.4s
346:	learn: 0.07

535:	learn: 0.0583608	total: 1.97s	remaining: 1.71s
536:	learn: 0.0582471	total: 1.98s	remaining: 1.7s
537:	learn: 0.0581929	total: 1.98s	remaining: 1.7s
538:	learn: 0.0581240	total: 1.98s	remaining: 1.7s
539:	learn: 0.0580749	total: 1.99s	remaining: 1.69s
540:	learn: 0.0579894	total: 1.99s	remaining: 1.69s
541:	learn: 0.0579360	total: 1.99s	remaining: 1.68s
542:	learn: 0.0578675	total: 2s	remaining: 1.68s
543:	learn: 0.0578209	total: 2s	remaining: 1.68s
544:	learn: 0.0577382	total: 2s	remaining: 1.67s
545:	learn: 0.0576832	total: 2s	remaining: 1.67s
546:	learn: 0.0576289	total: 2.01s	remaining: 1.66s
547:	learn: 0.0575588	total: 2.01s	remaining: 1.66s
548:	learn: 0.0574620	total: 2.02s	remaining: 1.66s
549:	learn: 0.0573635	total: 2.02s	remaining: 1.65s
550:	learn: 0.0572935	total: 2.02s	remaining: 1.65s
551:	learn: 0.0571667	total: 2.02s	remaining: 1.64s
552:	learn: 0.0571372	total: 2.03s	remaining: 1.64s
553:	learn: 0.0570190	total: 2.03s	remaining: 1.63s
554:	learn: 0.0569517	total

725:	learn: 0.0464970	total: 2.58s	remaining: 972ms
726:	learn: 0.0464929	total: 2.58s	remaining: 968ms
727:	learn: 0.0464507	total: 2.58s	remaining: 965ms
728:	learn: 0.0464466	total: 2.58s	remaining: 961ms
729:	learn: 0.0463570	total: 2.59s	remaining: 957ms
730:	learn: 0.0463170	total: 2.59s	remaining: 954ms
731:	learn: 0.0462960	total: 2.6s	remaining: 951ms
732:	learn: 0.0462731	total: 2.6s	remaining: 947ms
733:	learn: 0.0462103	total: 2.6s	remaining: 943ms
734:	learn: 0.0461579	total: 2.6s	remaining: 940ms
735:	learn: 0.0461107	total: 2.61s	remaining: 936ms
736:	learn: 0.0460732	total: 2.61s	remaining: 932ms
737:	learn: 0.0460670	total: 2.62s	remaining: 929ms
738:	learn: 0.0460199	total: 2.62s	remaining: 925ms
739:	learn: 0.0459633	total: 2.62s	remaining: 921ms
740:	learn: 0.0459080	total: 2.62s	remaining: 917ms
741:	learn: 0.0458173	total: 2.63s	remaining: 914ms
742:	learn: 0.0457559	total: 2.63s	remaining: 910ms
743:	learn: 0.0457379	total: 2.63s	remaining: 906ms
744:	learn: 0.04

927:	learn: 0.0380644	total: 3.37s	remaining: 262ms
928:	learn: 0.0380547	total: 3.38s	remaining: 258ms
929:	learn: 0.0380198	total: 3.38s	remaining: 254ms
930:	learn: 0.0379857	total: 3.38s	remaining: 251ms
931:	learn: 0.0379298	total: 3.39s	remaining: 247ms
932:	learn: 0.0379263	total: 3.39s	remaining: 244ms
933:	learn: 0.0378838	total: 3.4s	remaining: 240ms
934:	learn: 0.0378160	total: 3.4s	remaining: 236ms
935:	learn: 0.0377692	total: 3.4s	remaining: 233ms
936:	learn: 0.0377350	total: 3.4s	remaining: 229ms
937:	learn: 0.0376930	total: 3.41s	remaining: 225ms
938:	learn: 0.0376598	total: 3.41s	remaining: 222ms
939:	learn: 0.0376514	total: 3.41s	remaining: 218ms
940:	learn: 0.0376465	total: 3.42s	remaining: 214ms
941:	learn: 0.0376140	total: 3.42s	remaining: 211ms
942:	learn: 0.0375700	total: 3.42s	remaining: 207ms
943:	learn: 0.0375349	total: 3.43s	remaining: 203ms
944:	learn: 0.0374972	total: 3.43s	remaining: 200ms
945:	learn: 0.0374301	total: 3.43s	remaining: 196ms
946:	learn: 0.03

In [47]:
submit_predict = cat_model.predict(test)
submit_predict = np.exp(submit_predict)

In [64]:
submit_predict = np.expm1(blended_predictions(test))

In [66]:
submit['SalePrice'] = submit_predict

In [67]:
submit.to_csv('submit_catboost_best_data.csv', index=False)

XGB with initial with data model=0.13433 Kaggle = 0.14874

XGB with YoeJohnson skewness transformation = 0.136717 Kaggle = 0.14621

XGB with replacing categories with counts, instead of factorizing = 0.13647 Kaggle 0.16215 DON'T USE THIS

XGB with binary encoder and eliminating many new columns and all dropped columns = 0.13781 Kaggle = 0.1443 ALL OTHER SCORES WERE NOT GOOD, SO DON'T USE THIS

XGB not dropping outliers = 0.13462 Kaggle = 0.14215

Tried standard scaler and min-max scaler, but xgb couldn't run.

Catboost with XGB at 0.13462 = 0.12204 Kaggle = 0.1281

Catboost without eliminating negative xgb eli5 columns = 0.12181  Kaggle = 0.1279

Catboost with high NaN columns with 'None' instead of drop = 0.1214 Kaggle = 0.12854 BUT LOWER SCORES IN ALL MODELS

Catboost with garage columns as 'None' instead of mode = 0.1211 Kaggle = 0.12764

Catboost with Kfold splits at 20 = 0.12339 Kaggle = 0.12764

Kaggle with blended predictions model = 0.12167